# Building a Retrieval Augmented Generation (RAG) Chatbot

In [58]:
!pip install --quiet --upgrade langchain-text-splitters langchain-community langgraph
!pip install -qU langchain-mistralai
!pip install -qU langchain-chroma
!pip install xmltodict

# To correct UnstructuredXMLLoader errors
# !pip install "unstructured>=0.6.7"

## Setup

In [4]:
import getpass
import os

os.environ["LANGSMITH_TRACING"] = "true"
os.environ["LANGSMITH_API_KEY"] = getpass.getpass("Enter API key for Langsmith: ")

Enter API key for Langsmith:  ········


## Components

In [6]:
import getpass
import os

# Chat model

if not os.environ.get("MISTRAL_API_KEY"):
  os.environ["MISTRAL_API_KEY"] = getpass.getpass("Enter API key for Mistral AI: ")

Enter API key for Mistral AI:  ········


In [ ]:
from langchain_mistralai import ChatMistralAI, MistralAIEmbeddings

# Chat model
llm = ChatMistralAI(model="mistral-large-latest")

# Embeddings model
embeddings = MistralAIEmbeddings(model="mistral-embed")

In [8]:
from langchain_chroma import Chroma

# Vector store
vector_store = Chroma(embedding_function=embeddings)

## Loading JSON and XML files

Transforming the data JSON and XML files we got online into LangChain Document objects

### Test: loading a single JSON file

In [11]:
import json
from pathlib import Path
from pprint import pprint

file_path="../parcoursup/parcoursup_data.json"
data = json.loads(Path(file_path).read_text())
pprint(data)

[{'acceptations': 0,
  'annee_du_bac': 2021,
  'doublette': 'Art,Art',
  'formation': 'Licence Chimie',
  'propositions_d_admissions': 0.0,
  'voeux': 0},
 {'acceptations': 0,
  'annee_du_bac': 2021,
  'doublette': 'Art,Art',
  'formation': 'Licence Langues et littÃ©ratures franÃ§aises',
  'propositions_d_admissions': 0.0,
  'voeux': 0},
 {'acceptations': 0,
  'annee_du_bac': 2021,
  'doublette': 'Art,Art',
  'formation': 'Licence Philosophie, EpistÃ©mologie',
  'propositions_d_admissions': 0.0,
  'voeux': 0},
 {'acceptations': 0,
  'annee_du_bac': 2021,
  'doublette': 'Art,Art',
  'formation': 'Licence Physique',
  'propositions_d_admissions': 0.0,
  'voeux': 0},
 {'acceptations': 0,
  'annee_du_bac': 2021,
  'doublette': 'Art,Art',
  'formation': 'Licence Pluri Droit - Sciences Ã©co - AES',
  'propositions_d_admissions': 0.0,
  'voeux': 0},
 {'acceptations': 0,
  'annee_du_bac': 2021,
  'doublette': 'Art,Art',
  'formation': 'Licence Pluri Langues',
  'propositions_d_admissions': 0.0

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [12]:
from langchain_community.document_loaders import JSONLoader

loader = JSONLoader(
    file_path="../parcoursup/parcoursup_data.json",
    jq_schema=".[]",
    text_content=False
)

documents = loader.load()
pprint(documents[0])

Document(metadata={'source': 'C:\\Users\\Laura GALINDO\\Documents\\Academique_et_pro\\Epitech Digital School\\Bootcamp Chatbot IA\\chatbot-orientation-pro\\parcoursup\\parcoursup_data.json', 'seq_num': 1}, page_content='{"annee_du_bac": 2021, "doublette": "Art,Art", "formation": "Licence Chimie", "voeux": 0, "propositions_d_admissions": 0, "acceptations": 0}')


### Test: loading a single XML file

In [14]:
from bs4 import BeautifulSoup

with open('../onisep/Onisep_Fiches_Formations.xml', 'r', encoding="utf-8") as f:
    data = f.read()

bs_data = BeautifulSoup(data, 'xml')

print(bs_data.prettify()[:500])

<?xml version="1.0" encoding="utf-8"?>
<formations xmlns:exsl="http://exslt.org/common">
 <formation>
  <identifiant>
   FOR.1000
  </identifiant>
  <code_scolarite>
   16X20003
  </code_scolarite>
  <libelle_complet>
   mastère spé. management de la qualité, de la sécurité et de l'environnement
  </libelle_complet>
  <sigle/>
  <libelle_generique/>
  <libelle_specifique/>
  <type_option/>
  <type_Formation>
   <type_formation_sigle>
    mastère spé.
   </type_formation_sigle>
   <type_formation


In [15]:
from langchain_community.document_loaders import UnstructuredXMLLoader
from pprint import pprint

loader = UnstructuredXMLLoader('../onisep/Onisep_Fiches_Formations.xml')

documents = loader.load()

print(documents[0].page_content[:500])

FOR.1000

16X20003

mastère spé. management de la qualité, de la sécurité et de l'environnement

mastère spé.

MASTERE SPE

mastère spécialisé

"1 an"

https://www.francecompetences.fr/recherche/rncp/37084/

200

Spécialités pluritechnologiques de la production

R

Contrôle, prévention, entretien

niveau 7

REF.423

bac + 6

16X

Label de la Conférence des grandes écoles (CGE)

Formation inscrite au RNCP

MET.878

chargé/e hygiène sécurité environnement (HSE)

chargée hygiène sécurité environnem


### Converting XML files to JSON files

The layout of Document objects loaded from XML files is too different from JSON files, and less well structured, so the MistralAI API cannot later embed them into the vector store

In [81]:
import json
import xmltodict

def convert_xml_to_json(xml_file: str, json_file: str):
    """
    Convert an XML file to a JSON file
    
    Parameters:
        - xml_file (str): Path to the input XML file
        - json_file (str): Path to the output JSON file
    """
    try:
        # Open and read the XML file
        with open(xml_file, 'r', encoding='utf-8') as f:
            xml_content = f.read()

        # Parse the XML content into a dictionary
        data_dict = xmltodict.parse(xml_content)

        # Write the dictionary to a JSON file with indentation for readability
        with open(json_file, 'w', encoding='utf-8') as f:
            json.dump(data_dict, f, ensure_ascii=False, indent=4)

        print(f"Converted '{xml_file}' to '{json_file}' successfully")

    except Exception as e:
        print(f"Error converting '{xml_file}' to JSON: {e}")

In [83]:
xml_file = '../onisep/Onisep_Fiches_Formations.xml'
json_file = '../onisep/Onisep_Fiches_Formations.json'
convert_xml_to_json(xml_file, json_file)

xml_file = '../onisep/Onisep_Fiches_Metiers.xml'
json_file = '../onisep/Onisep_Fiches_Metiers.json'
convert_xml_to_json(xml_file, json_file)

Converted '../onisep/Onisep_Fiches_Formations.xml' to '../onisep/Onisep_Fiches_Formations.json' successfully
Converted '../onisep/Onisep_Fiches_Metiers.xml' to '../onisep/Onisep_Fiches_Metiers.json' successfully


### Loading multiple JSON files as LangChain Document objects

In [101]:
import os
import json
from pathlib import Path
from langchain.docstore.document import Document
from langchain_community.document_loaders import JSONLoader, UnstructuredXMLLoader

# To correct UnstructuredXMLLoader errors
# import nltk
# nltk.download('punkt')
# nltk.download('averaged_perceptron_tagger')

def load_json_documents(file_path: str) -> list:
    """
    Load a JSON file using JSONLoader and return a list of Documents
    """
    loader = JSONLoader(
        file_path=file_path,
        jq_schema=".[]",
        text_content=False,
    )
    try:
        documents = loader.load()
        print(f"[JSON] Loaded file: {file_path} ({len(documents)} document(s))")
        return documents
    except Exception as e:
        print(f"Error while loading JSON file {file_path} : {e}")
        return []

# def load_xml_documents(file_path: str) -> list:
#    """
#    Load an XML file using UnstructuredXMLLoader and return a list of Documents
#    """
#    loader = UnstructuredXMLLoader(file_path)
#    try:
#        documents = loader.load()
#        print(f"[XML] Loaded file: {file_path} ({len(documents)} document(s))")
#        return documents
#    except Exception as e:
#        print(f"Error while loading XML file {file_path} : {e}")
#        return []

def load_documents(file_paths: list) -> list:
    """
    For each file in the list, we determine its extension and call the appropriate loader
    (JSONLoader or UnstructuredXMLLoader), and then return a complete list of Documents
    """
    documents = []
    for fp in file_paths:
        ext = Path(fp).suffix.lower()
        if ext == ".json":
            documents.extend(load_json_documents(fp))
#        elif ext == ".xml":
#            documents.extend(load_xml_documents(fp))
        else:
            print(f"Unsupported file (extension {ext}) : {fp}")
    return documents

def export_documents(documents: list):
    """
    Save the Document objects to a text file for inspection or debugging
    """
    with open("loaded_documents.txt", "w", encoding="utf-8") as f:
        for doc in documents:
            f.write(f"Source: {doc.metadata.get('source')}\n")
            f.write(f"Content:\n{doc.page_content}\n\n---\n\n")
    
    print("Documents saved to 'loaded_documents.txt'")

In [109]:
# List of JSON and XML files to load
file_list = [
    # DONE:
    # "../parcoursup/parcoursup_data.json",
    # "../mon_master/monmaster_data.json",
    # TODO:
    "../onisep/Onisep_Fiches_Formations.json",
    "../onisep/Onisep_Fiches_Metiers.json"
]

# Load all the documents
all_documents = load_documents(file_list)

print(f"\nTotal number of loaded documents: {len(all_documents)}")

export_documents(all_documents)

[JSON] Loaded file: ../onisep/Onisep_Fiches_Formations.json (1 document(s))
[JSON] Loaded file: ../onisep/Onisep_Fiches_Metiers.json (1 document(s))

Total number of loaded documents: 2
Documents saved to 'loaded_documents.txt'


In [111]:
from langchain_text_splitters import RecursiveCharacterTextSplitter

def dynamic_split_documents(documents, base_chunk_size=1000, min_chunks=3, max_chunks=200):
    """
    Dynamically split a list of documents into smaller chunks based on document size
    
    Parameters:
        - documents: List of LangChain Document objects
        - base_chunk_size: Default chunk size in characters
        - min_chunks: Minimum number of chunks per document
        - max_chunks: Maximum number of chunks per document
    
    Returns:
        - List of split documents
    """
    all_splits = []
    
    for doc in documents:
        doc_length = len(doc.page_content)
        
        # Dynamically adjust the chunk size:
        # - Ensure chunks are not too small by using at least `base_chunk_size`
        # - Ensure chunks are not too big by keeping at least `min_chunks` per document
        # - This balances the number and size of chunks for better retrieval
        chunk_size = max(base_chunk_size, doc_length // max_chunks)  # Prevents chunks from being too tiny
        chunk_size = min(chunk_size, doc_length // min_chunks)  # Ensures we don't have too few large chunks
        
        # Define the text splitter
        text_splitter = RecursiveCharacterTextSplitter(
            chunk_size=chunk_size,
            chunk_overlap=chunk_size // 5,  # 20% overlap
            add_start_index=True # Keeps track of where in the original document each chunk came from
        )
        
        # Split the document and extend the list
        splits = text_splitter.split_documents([doc])
        # print(f"Document: {doc.metadata.get('source')} | Original Length: {len(doc.page_content)} | Chunks Created: {len(splits)}")
        
        all_splits.extend(splits) # Adds all the elements in splits to all_splits, one by one
    
    print(f"\nTotal number of chunks created: {len(all_splits)}")
    return all_splits

def export_split_documents(chunks):
    """
    Save the split documents to a text file with delimiters between chunks

    Each document chunk's source and content are written to 'split_documents.txt', 
    with '---' as a separator between different chunks.

    Parameters:
        - chunks (list): A list of LangChain Document objects after splitting

    Output:
        - File containing all split document chunks with delimiters
    """
    with open("split_documents.txt", "w", encoding="utf-8") as f:
        for i, chunk in enumerate(chunks):
            # Add delimiter before every chunk except the first one
            if i > 0:
                f.write("\n---\n\n")

            f.write(f"Source: {chunk.metadata.get('source')}\n")
            f.write(f"Content:\n{chunk.page_content}\n")

    print("Split documents saved to 'split_documents.txt'")

In [113]:
# Split the loaded documents
split_documents = dynamic_split_documents(all_documents)

export_split_documents(split_documents)


Total number of chunks created: 500
Split documents saved to 'split_documents.txt'


## Storing Document splits

Indexing our chunks of documents to be able to vector search over them at runtime, which entails embedding the contents of each chunk of Document into the Chroma vector store

In [23]:
import time

batch_size = 10  # Process 10 chunks of documents at a time

for i in range(0, len(split_documents), batch_size):
     batch = [doc for doc in split_documents[i:i + batch_size] if len(doc.page_content.strip()) > 10]  

    if not batch:
        print(f"Skipping empty batch {i//batch_size + 1}")
        continue  # Skip processing if batch is empty
    
    try:
        document_ids = vector_store.add_documents(documents=batch)
        print(f"Batch {i//batch_size + 1}: {document_ids[:3]}")
    except Exception as e:
        print(f"Error in batch {i//batch_size + 1}: {e}")
    
    time.sleep(2)  # Wait 2 seconds before the next batch

Batch 1: ['e4e290e7-3ad0-4d26-8c13-078ae83824f4', '719fe31e-7cbd-4152-9cf2-5262553ffa01', '0493492c-a637-4bcb-a4f7-2f597daca379']
Batch 2: ['e5f77537-85ef-4f34-aff0-363cacea1bde', 'fbe2271e-0e23-4ea2-ba17-b123030ba502', '08b201ae-99f7-4e6e-816d-39bdafb8973f']
Batch 3: ['895ed64f-8598-4ead-bc3c-1ca658ce5249', '47841687-c351-4b7f-9d73-0525cdf5fa7c', '4eb28f8d-692d-45e6-9ce5-1923424e1996']
Batch 4: ['672fd908-9ff9-45b8-abb6-c32d9dda1ea1', 'c52f9663-bab3-46a7-9813-9f0070d94350', '68411707-5536-4bac-83b3-191e0b1f4f83']
Batch 5: ['5ed49deb-2601-4586-9940-04aaa6b365af', 'fbe995aa-7adc-40e3-a586-c35b649757d3', 'e30d0280-519d-4bd8-aa43-db34cefb7319']
Batch 6: ['8d23730b-b8e0-4c0f-b819-1aa2ee9b0cae', '5490c4cc-12ca-4817-b27b-96eee03a7f57', '82aee1a9-d916-4aae-bb87-a0e29e12043a']
Batch 7: ['2c0b0c90-66bc-4a4d-bb3b-deee8947624e', '301e314f-e85c-4d97-9274-86a07f7eb0cd', 'c29c8d6d-975f-4380-90b1-91c9603d25ee']
Batch 8: ['3b836467-4f2d-424b-b03d-d65ec5b3a343', '78cad6ef-f8ea-4dd9-b7c4-764e09ca0eb8', 

An error occurred with MistralAI: [Errno 11001] getaddrinfo failed


Error in batch 2113: [Errno 11001] getaddrinfo failed
Batch 2114: ['46fa584f-cb3c-4cfc-a59c-381f704550e5', 'bd984ae4-f83b-447a-806c-fd8b63595893', 'a677b2bd-0324-4377-9e5b-c08ee7cde52f']
Batch 2115: ['d98b693b-b274-4732-870b-4cd7695e4fbd', '1aad44a6-eaf8-4f4f-97aa-c34a8ead1425', '18520cee-12f4-419b-9823-c7a020481bbf']
Batch 2116: ['2b34a7cb-3712-4676-a967-acccb43c4280', 'ec96fdc9-3688-45ab-8279-d56e71899006', '7e164f50-7cf4-472f-99e6-7f26d6630cf4']
Batch 2117: ['a425dc3c-45c4-4304-aa6c-fcc578229a48', 'f4c5d1fa-81dd-42ab-b02d-6daf86bcb8ad', '7ae1e7df-bbc7-49f2-8314-757ae275bd8b']
Batch 2118: ['cf1bdc46-2589-4ca4-aa8a-e62c29c14def', '054ffa6a-2940-4810-a131-7f73d5316db8', '00a826df-974b-43c7-baa4-b14e6e9d79fc']
Batch 2119: ['329b7a44-90a3-424e-9ba8-cd4d43b78799', '4968b3c8-7414-4a23-8626-42cffe715c5e', 'd02b2693-1af0-45b2-97e0-aeb0a06656c0']
Batch 2120: ['70c8797d-3096-4303-8901-a70b052cbc8f', '76e9f552-d373-4053-b55a-92ff646045bb', 'f5e0890f-9a43-4fae-b36f-c449133bc501']
Batch 2121: ['b

An error occurred with MistralAI: [Errno 11001] getaddrinfo failed


Error in batch 9228: [Errno 11001] getaddrinfo failed


...

Error in batch 12978: Client error '400 Bad Request' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/400


An error occurred with MistralAI: Client error '400 Bad Request' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/400


Error in batch 12979: Client error '400 Bad Request' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/400


An error occurred with MistralAI: Client error '400 Bad Request' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/400


Error in batch 12980: Client error '400 Bad Request' for url 'https://api.mistral.ai/v1/embeddings'
For more information check: https://developer.mozilla.org/en-US/docs/Web/HTTP/Status/400
Batch 12981: ['edb6100d-9927-40f8-a63f-2798707de0e4']


## Creating the RAG chain with LangChain

Creating a retrieval chain that, based on a user question, will retrieve relevant Documents from Chroma and provide them in context to the MistralAI language model to generate an informed answer

In [ ]:
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain.chains import create_retrieval_chain
from langchain import hub

# Interface that interrogates the vector store
retriever = vecteur_store.as_retriever(search_kwargs={"k": 5})  # the k most relevant chunks of documents

# Load a pre-defined prompt template for retrieval-based Q&A.
# This template helps structure the input for the AI model.
retrieval_chat_prompt = hub.pull("langchain-ai/retrieval-qa-chat")

# Create a document combination chain.
# This step tells the AI how to process and merge the retrieved documents
# before generating an answer.
combine_docs_chain = create_stuff_documents_chain(llm, retrieval_chat_prompt)

# Create the retrieval chain.
# This connects the retriever with the AI model.
retrieval_chain = create_retrieval_chain(retriever, combine_docs_chain)

In [ ]:
# Example usage
response = retrieval_chain.invoke({"input": "..."})
print(response)

In [ ]:
question = "Quelles formations sont recommandées pour un profil INFP qui souhaite travailler dans l’éducation ?"
reponse = retrieval_chain.run(question)
print(reponse)